In [1]:
import $ivy.`org.plotly-scala::plotly-almond:0.7.6`
import $ivy.`org.scalanlp::breeze:1.0`
kernel.silent(true)

import $ivy.$                                      

import $ivy.$                         


In [2]:
import breeze.linalg._
import breeze.stats.regression._
import breeze.numerics._
import breeze.stats._
import breeze.stats.distributions._
import breeze.stats.DescriptiveStats._
import scala.io.Source

import plotly._, plotly.element._, plotly.layout._, plotly.Almond._

type DMatrix = breeze.linalg.DenseMatrix[Double]
type DVector = breeze.linalg.DenseVector[Double]

In [3]:
/**
 * Hold data and help to describe it
 *
 * @param header columns name list
 * @param X      features data matrix
 * @param y      target vector
 */
case class DataFrame(header: Array[String], X: DMatrix, y: DVector) {
  /**
   * Print column description and plot columns data histogram
   *
   * @param column              columns index
   * @param hist_max_percentile columns data will be clipped 
   *                            due to handle long tail on hist
   */
  def describe(column: Int, hist_max_percentile: Double = 0.95) {
    println(s"Columns:" + header(column))
    println(s"Min:${X(::, column).min}")
    println(s"Mean:${mean(X(::, column))}")
    println(s"Max:${X(::, column).max}")
    val max_p = percentile(X(::, column).toScalaVector, hist_max_percentile)
    val hist = Histogram(
      X(::, column).toScalaVector.map(x => x.min(max_p)).toSeq
    )

    val data = Seq(hist)

    val layout = Layout(
      title = "Histogram"
    )

    plot(data, layout)
  }
}

/**
 * Read csv and transform it to features and target
 *
 * @param filename dataset filename
 * @param sep      csv separator char
 * @return dataset
 */
def read_csv(filename: String, sep: Char): DataFrame = {
  val raw = (for (line <- Source.fromFile(filename).getLines) yield line.split(sep).map(_.trim)).toList
  val header = raw.head
  val data = raw.tail.map(_.map(x => if (x.isEmpty) Double.NaN else x.toDouble))

  val m = DenseMatrix(data: _*)
  val X = m(::, 0 to -2).toDenseMatrix
  val y = m(::, -1).toDenseVector
  DataFrame(header.dropRight(1), X, y)
} 

In [4]:
/**
 * Split data into train-test sets
 *
 * @param X features matrix
 * @param y target vector
 * @return train and test features and targets
 */
def train_test_split(X: DMatrix, y: DVector): (DMatrix, DVector, DMatrix, DVector) = {
  val index = DenseVector[Int]((for (x <- 0 until X.rows) yield x): _*)
  val train_x = X((index % 5) :!= 0, ::).toDenseMatrix
  val train_y = y((index % 5) :!= 0).toDenseVector
  val test_x = X((index % 5) :== 0, ::).toDenseMatrix
  val test_y = y((index % 5) :== 0).toDenseVector
  (train_x, train_y, test_x, test_y)
}

In [5]:
/**
 * Calculate metric value
 *
 * @param y_true ground truth vector
 * @param y_pred prediction vector
 * @return metric value
 */
def metric(y_true: DVector, y_pred: DVector): Double = {
  mean(pow(y_true - y_pred, 2.0))
}

In [6]:
/**
 * Plot chart to understand model performance
 *
 * @param modelName name of regression model
 * @param y_true    ground truth
 * @param y_pred    prediction vector
 * @param metric    metric function
 */
def explain(modelName: String, y_true: DVector, y_pred: DVector, metric: (DVector, DVector) => Double) {
  println(s"Model: $modelName")
  println("RMSE:" + metric(y_true, y_pred))
  val trace = Scatter(
    y_true.toScalaVector,
    y_pred.toScalaVector,
    mode = ScatterMode(ScatterMode.Markers)
  )

  val data = Seq(trace)

  val layout = Layout(
    title = "Modeling results"
  )

  plot(data, layout)
}

In [7]:
/**
 *
 * @param modelName regression model name
 * @param transform preprocessing function
 * @param split     train-test split function
 * @param fit       fit function - return function which can predict outcome from data
 * @param metric    metric function
 */
class Pipeline(modelName: String,
               transform: (DMatrix) => DMatrix,
               split: (DMatrix, DVector) => (DMatrix, DVector, DMatrix, DVector),
               fit: (DMatrix, DVector) => ((DMatrix) => DVector),
               metric: (DVector, DVector) => Double) {
  def apply(X: DMatrix, y: DVector) = {
    val (train_x, train_y, test_x, test_y) = split(transform(X), y)
    val predict = fit(train_x, train_y)
    explain(modelName, test_y, predict(test_x), metric)
  }
}

In [8]:
/**
 * Default breeze regression
 *
 * @param X input data
 * @param y ground truth
 * @return prediction function
 */
def breezeRegressionFit(X: DMatrix, y: DVector): (DMatrix) => DVector = {
  val result = leastSquares(X, y)
  (X_test: DMatrix) => result(X_test)
}

val breezeRegression =
  new Pipeline(
    "breezeRegression",
    transform = x => x.map(e => if (!e.isNaN) e else 0),
    split = train_test_split,
    fit = breezeRegressionFit,
    metric = metric)

In [9]:
/**
 * Generate random index form random batch sampling 
 *
 * @param len
 * @param size
 * @return random index
 */
def random_index(len: Int, size: Int) = {
  scala.util.Random.shuffle((0 until len).toList).take(size)
}

/**
 * SGD mini-batch regression
 *
 * @param lr        learning rate
 * @param batchSize batch size
 * @param nIter     number of iteration
 * @return prediction function
 */
def sgdRegressionFit(lr: Double = 0.01,
                     batchSize: Int = 256,
                     nIter: Int = 10): (DMatrix, DVector) => ((DMatrix) => DVector) = {
  def sgd(X: DMatrix, y: DVector, coef: DVector, lr: Double, batchSize: Int, nIter: Int): DVector = nIter match {
    case 0 => coef
    case nIter => {
      val rand_index = random_index(X.rows, batchSize)
      val batch_x = X(rand_index, ::).toDenseMatrix
      val batch_y = y(rand_index).toDenseVector
      val grad = batch_x(::, *) * (batch_x * coef - batch_y) * 2.0

      sgd(X, y, coef - mean(grad(::, *)).t * lr, lr, batchSize, nIter - 1)
    }
  }

  def fit(X: DMatrix, y: DVector): (DMatrix) => DVector = {
    val coef_init = breeze.linalg.DenseVector[Double](new Gaussian(0, 1).sample(X.cols): _*)
    val coef = sgd(X, y, coef_init, lr, batchSize, nIter)
    (X_test: DMatrix) => X_test * coef
  }

  fit
}

val sgdRegression =
  new Pipeline(
    "sgdRegression",
    transform = x => x.map(e => if (!e.isNaN) e else 0),
    split = train_test_split,
    fit = sgdRegressionFit(),
    metric = metric)

/**
 * Standard scaling preprocessing
 *
 * @param X input data
 * @return preprocessed data
 */
def sgdPreprocess(X: DMatrix): DMatrix = {
  def normalize(v: DVector): DVector = {
    (v - mean(v)) / stddev(v)
  }

  val Xna = X.map(e => if (!e.isNaN) e else 0).toDenseMatrix
  val Xna1 = Xna(::, *).map(normalize(_))
  DenseMatrix.horzcat(DenseMatrix.ones[Double](Xna1.rows, 1), Xna1)
}

val adjustedSgdRegression =
  new Pipeline(
    "adjustedSgdRegression",
    transform = sgdPreprocess,
    split = train_test_split,
    fit = sgdRegressionFit(lr = 0.01, nIter = 100),
    metric = metric)

In [52]:
/**
 * Regression based on pseudo inverse matrix
 *
 * @param batchSize batch size due to java memory error avoiding
 * @return prediction function
 */
def pseudoInverseMatrixFit(batchSize: Int = 256): (DMatrix, DVector) => ((DMatrix) => DVector) = {
  def fit(X: DMatrix, y: DVector): (DMatrix) => DVector = {
    val idx = random_index(X.rows, batchSize)
    val coef = pinv(X(idx, ::).toDenseMatrix) * y(idx).toDenseVector
    (X_test: DMatrix) => X_test * coef
  }

  fit
}

val pseudoInverseMatrix =
  new Pipeline(
    "pseudoInverseMatrix",
    transform = sgdPreprocess,
    split = train_test_split,
    fit = pseudoInverseMatrixFit(10000),
    metric = metric)

In [10]:
val df = read_csv("Dataset.csv", ',')

In [11]:
df.describe(0)

Columns:likes
Min:36.0
Mean:1313813.7475396227
Max:4.86972297E8


In [12]:
df.describe(1)

Columns:Checkins
Min:0.0
Mean:4676.133751739932
Max:186370.0


In [13]:
df.describe(10)

Columns:length
Min:0.0
Mean:163.65247014579123
Max:21480.0


In [14]:
breezeRegression(df.X, df.y)

Nov 26, 2020 6:36:22 AM com.github.fommil.netlib.LAPACK <clinit>
Nov 26, 2020 6:36:22 AM com.github.fommil.netlib.LAPACK <clinit>
Nov 26, 2020 6:36:22 AM com.github.fommil.netlib.BLAS <clinit>
Nov 26, 2020 6:36:22 AM com.github.fommil.netlib.BLAS <clinit>


Model: breezeRegression
RMSE:989.9257127963587


In [15]:
sgdRegression(df.X, df.y)

Model: sgdRegression
RMSE:3.282366550742108E235


In [16]:
adjustedSgdRegression(df.X, df.y)

Model: adjustedSgdRegression
RMSE:1006.0916141577156


In [53]:
pseudoInverseMatrix(df.X, df.y)

Model: pseudoInverseMatrix
RMSE:995.8093122116464
